https://www.tensorflow.org/tutorials/layers

In [1]:
from __future__ import absolute_import
from __future__ import division
from __future__ import print_function

# Imports
import numpy as np
import tensorflow as tf

tf.logging.set_verbosity(tf.logging.INFO)




/anaconda3/lib/python3.6/importlib/_bootstrap.py:205: RuntimeWarning: compiletime version 3.5 of module 'tensorflow.python.framework.fast_tensor_util' does not match runtime version 3.6
  return f(*args, **kwds)


preprocess the image by adding filters

In [2]:
def cnn_model_fn(features, labels, mode):
  """Model function for CNN."""
  # Input Layer
  # Reshape X to 4-D tensor: [batch_size, width, height, channels]
  # MNIST images are 28x28 pixels, and have one color channel
  input_layer = tf.reshape(features["x"], [-1, 28, 28, 1])

  # Convolutional Layer #1
  # Computes 32 features using a 5x5 filter with ReLU activation.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 28, 28, 1]
  # Output Tensor Shape: [batch_size, 28, 28, 32]
  conv1 = tf.layers.conv2d(
      inputs=input_layer,
      filters=32,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #1
  # First max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 28, 28, 32]
  # Output Tensor Shape: [batch_size, 14, 14, 32]
  pool1 = tf.layers.max_pooling2d(inputs=conv1, pool_size=[2, 2], strides=2)

  # Convolutional Layer #2
  # Computes 64 features using a 5x5 filter.
  # Padding is added to preserve width and height.
  # Input Tensor Shape: [batch_size, 14, 14, 32]
  # Output Tensor Shape: [batch_size, 14, 14, 64]
  conv2 = tf.layers.conv2d(
      inputs=pool1,
      filters=64,
      kernel_size=[5, 5],
      padding="same",
      activation=tf.nn.relu)

  # Pooling Layer #2
  # Second max pooling layer with a 2x2 filter and stride of 2
  # Input Tensor Shape: [batch_size, 14, 14, 64]
  # Output Tensor Shape: [batch_size, 7, 7, 64]
  pool2 = tf.layers.max_pooling2d(inputs=conv2, pool_size=[2, 2], strides=2)

  # Flatten tensor into a batch of vectors
  # Input Tensor Shape: [batch_size, 7, 7, 64]
  # Output Tensor Shape: [batch_size, 7 * 7 * 64]
  pool2_flat = tf.reshape(pool2, [-1, 7 * 7 * 64])

  # Dense Layer
  # Densely connected layer with 1024 neurons
  # Input Tensor Shape: [batch_size, 7 * 7 * 64]
  # Output Tensor Shape: [batch_size, 1024]
  dense = tf.layers.dense(inputs=pool2_flat, units=1024, activation=tf.nn.relu)

  # Add dropout operation; 0.6 probability that element will be kept
  dropout = tf.layers.dropout(
      inputs=dense, rate=0.4, training=mode == tf.estimator.ModeKeys.TRAIN)

  # Logits layer
  # Input Tensor Shape: [batch_size, 1024]
  # Output Tensor Shape: [batch_size, 10]
  logits = tf.layers.dense(inputs=dropout, units=10)

  predictions = {
      # Generate predictions (for PREDICT and EVAL mode)
      "classes": tf.argmax(input=logits, axis=1),
      # Add `softmax_tensor` to the graph. It is used for PREDICT and by the
      # `logging_hook`.
      "probabilities": tf.nn.softmax(logits, name="softmax_tensor")
  }
  if mode == tf.estimator.ModeKeys.PREDICT:
    return tf.estimator.EstimatorSpec(mode=mode, predictions=predictions)

  # Calculate Loss (for both TRAIN and EVAL modes)
  loss = tf.losses.sparse_softmax_cross_entropy(labels=labels, logits=logits)

  # Configure the Training Op (for TRAIN mode)
  if mode == tf.estimator.ModeKeys.TRAIN:
    optimizer = tf.train.GradientDescentOptimizer(learning_rate=0.001)
    train_op = optimizer.minimize(
        loss=loss,
        global_step=tf.train.get_global_step())
    return tf.estimator.EstimatorSpec(mode=mode, loss=loss, train_op=train_op)

  # Add evaluation metrics (for EVAL mode)
  eval_metric_ops = {
      "accuracy": tf.metrics.accuracy(
          labels=labels, predictions=predictions["classes"])}
  return tf.estimator.EstimatorSpec(
      mode=mode, loss=loss, eval_metric_ops=eval_metric_ops)



In [3]:
  mnist = tf.contrib.learn.datasets.load_dataset("mnist")
  train_data = mnist.train.images  # Returns np.array
  train_labels = np.asarray(mnist.train.labels, dtype=np.int32)
  eval_data = mnist.test.images  # Returns np.array
  eval_labels = np.asarray(mnist.test.labels, dtype=np.int32)

  # Create the Estimator
  mnist_classifier = tf.estimator.Estimator(
      model_fn=cnn_model_fn, model_dir="/tmp/mnist_convnet_model")

  # Set up logging for predictions
  # Log the values in the "Softmax" tensor with label "probabilities"
  tensors_to_log = {"probabilities": "softmax_tensor"}
  logging_hook = tf.train.LoggingTensorHook(
      tensors=tensors_to_log, every_n_iter=50)

  # Train the model
  train_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": train_data},
      y=train_labels,
      batch_size=100,
      num_epochs=None,
      shuffle=True)
  mnist_classifier.train(
      input_fn=train_input_fn,
      steps=20000,
      hooks=[logging_hook])

  # Evaluate the model and print results
  eval_input_fn = tf.estimator.inputs.numpy_input_fn(
      x={"x": eval_data},
      y=eval_labels,
      num_epochs=1,
      shuffle=False)
  eval_results = mnist_classifier.evaluate(input_fn=eval_input_fn)
  print(eval_results)

Successfully downloaded train-images-idx3-ubyte.gz 9912422 bytes.
Extracting MNIST-data/train-images-idx3-ubyte.gz
Successfully downloaded train-labels-idx1-ubyte.gz 28881 bytes.
Extracting MNIST-data/train-labels-idx1-ubyte.gz
Successfully downloaded t10k-images-idx3-ubyte.gz 1648877 bytes.
Extracting MNIST-data/t10k-images-idx3-ubyte.gz
Successfully downloaded t10k-labels-idx1-ubyte.gz 4542 bytes.
Extracting MNIST-data/t10k-labels-idx1-ubyte.gz
INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': '/tmp/mnist_convnet_model', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': None, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x126b7d748>, '_task_type': 'worker', '_task_id': 0, '_master': '', '_is_chief': True, '_num_ps_replic

INFO:tensorflow:loss = 2.311, step = 1
INFO:tensorflow:probabilities = [[ 0.10746595  0.12016373  0.09716576  0.08351712  0.10720523  0.09953511
   0.09043945  0.09013243  0.0997127   0.10466248]
 [ 0.09094688  0.10251177  0.10201128  0.08728684  0.11120359  0.08584564
   0.10514792  0.09813932  0.10477488  0.11213188]
 [ 0.09936196  0.11197553  0.09266675  0.09908188  0.10050853  0.08820403
   0.1021539   0.10035967  0.09839123  0.10729665]
 [ 0.10998619  0.10358881  0.1101011   0.08587981  0.09683325  0.08979144
   0.09845117  0.10340219  0.10584631  0.09611969]
 [ 0.10249295  0.11616302  0.10355543  0.08375052  0.10488812  0.0988131
   0.08677506  0.09212258  0.09571482  0.11572447]
 [ 0.09686998  0.09821053  0.11044745  0.08711649  0.09694616  0.09753673
   0.09438644  0.09823419  0.10856025  0.11169183]
 [ 0.08511797  0.10681958  0.10324617  0.09379271  0.10739812  0.09841032
   0.09449621  0.09930158  0.10588697  0.1055304 ]
 [ 0.09603963  0.1055238   0.10685601  0.09240913  0.11

INFO:tensorflow:global_step/sec: 3.73351
INFO:tensorflow:probabilities = [[ 0.11012814  0.11373439  0.0998264   0.09128255  0.09575511  0.0992107
   0.09865049  0.09386337  0.09113327  0.10641552]
 [ 0.10620268  0.09708013  0.10537681  0.09535135  0.12009574  0.09915528
   0.08872589  0.09525454  0.09086385  0.10189368]
 [ 0.10632656  0.10998951  0.1051838   0.0914753   0.11158187  0.0995502
   0.07935401  0.0943856   0.08709469  0.1150584 ]
 [ 0.09138551  0.09896103  0.10941853  0.0894552   0.10042751  0.11237071
   0.10599825  0.08758537  0.1049995   0.09939837]
 [ 0.09764536  0.10326787  0.10657887  0.09038384  0.10118275  0.1029958
   0.0823831   0.09876426  0.09995697  0.11684121]
 [ 0.10615676  0.10339961  0.10519228  0.08918645  0.10950054  0.08787367
   0.08330525  0.08738686  0.10012132  0.12787727]
 [ 0.09245948  0.10067807  0.10694619  0.09398165  0.10957064  0.10585321
   0.10825305  0.07848986  0.08885034  0.11491749]
 [ 0.10965703  0.10123857  0.10588272  0.08946461  0.10

INFO:tensorflow:loss = 2.29896, step = 101 (26.781 sec)
INFO:tensorflow:probabilities = [[ 0.09908714  0.10506508  0.09728374  0.09603979  0.11283348  0.09298699
   0.09512126  0.09489372  0.09164968  0.11503919]
 [ 0.09858163  0.11326917  0.09335344  0.08771203  0.10253401  0.08762003
   0.09401894  0.09468964  0.11400527  0.11421585]
 [ 0.11800841  0.09749915  0.08873615  0.10398402  0.0976493   0.09749555
   0.09889639  0.09461582  0.09506492  0.10805026]
 [ 0.09553672  0.10267115  0.10408112  0.10250898  0.09715304  0.10245658
   0.08595298  0.10174174  0.09834431  0.10955346]
 [ 0.08342104  0.1038831   0.11508233  0.10098245  0.11289001  0.09080085
   0.09231638  0.08749101  0.09869789  0.11443496]
 [ 0.10375743  0.10254588  0.1079193   0.09679948  0.10219108  0.10475186
   0.08885452  0.08888885  0.0931164   0.11117521]
 [ 0.09965947  0.10180984  0.10677292  0.08788107  0.10699754  0.10442227
   0.09831647  0.09987243  0.09706127  0.09720665]
 [ 0.09869608  0.10149677  0.10039755

INFO:tensorflow:global_step/sec: 3.76448
INFO:tensorflow:probabilities = [[ 0.09591985  0.10844029  0.10635034  0.09285586  0.10800025  0.08357673
   0.09952661  0.0952493   0.1061749   0.10390588]
 [ 0.09941206  0.10363628  0.10583752  0.08986977  0.11533853  0.08207685
   0.10575964  0.09795156  0.09483409  0.10528376]
 [ 0.11899637  0.09806953  0.10069836  0.09768754  0.09267047  0.08835928
   0.09515005  0.09309541  0.10305829  0.11221465]
 [ 0.09498623  0.1079865   0.10041425  0.09119382  0.10703697  0.09442566
   0.09577085  0.09406053  0.10468864  0.10943658]
 [ 0.10149023  0.08988706  0.09806377  0.10072492  0.09956228  0.10217761
   0.08906294  0.09093928  0.11049831  0.11759353]
 [ 0.09511625  0.10771955  0.09849627  0.09233523  0.09709109  0.096264
   0.10297596  0.1014406   0.1071166   0.10144448]
 [ 0.10820266  0.09790323  0.09436774  0.09400391  0.09825992  0.09579861
   0.09681688  0.09329664  0.10946672  0.11188365]
 [ 0.09628108  0.09914307  0.11412292  0.08645154  0.1

...

INFO:tensorflow:global_step/sec: 3.58575
INFO:tensorflow:probabilities = [[ 0.01006312  0.00002537  0.00343459  0.00024664  0.05998822  0.83942312
   0.07943505  0.00007516  0.00437269  0.00293592]
 [ 0.99985123  0.00000002  0.0001196   0.00000066  0.00000001  0.00000167
   0.00000188  0.00000454  0.00000002  0.00002042]
 [ 0.00021934  0.0000063   0.00008792  0.00062459  0.00000185  0.99872595
   0.00004662  0.00001075  0.00025951  0.00001713]
 [ 0.00000448  0.0000012   0.00007996  0.000054    0.00306273  0.0002709
   0.00000287  0.00087348  0.00050073  0.99514967]
 [ 0.00147784  0.00041457  0.00179701  0.00817898  0.02334586  0.0036895
   0.00024323  0.06280836  0.00147689  0.89656776]
 [ 0.00349768  0.00006899  0.00607089  0.00018561  0.00114535  0.00014119
   0.00722842  0.00000294  0.98068595  0.00097305]
 [ 0.00207244  0.74186915  0.01841338  0.01731416  0.03148955  0.0572224
   0.03532034  0.00164358  0.09072661  0.00392841]
 [ 0.00031891  0.00152496  0.01505092  0.00744673  0.00

INFO:tensorflow:loss = 0.191865, step = 19801 (27.884 sec)
INFO:tensorflow:probabilities = [[ 0.00345113  0.08064785  0.04896175  0.04258159  0.00335745  0.00654597
   0.00013048  0.75797021  0.03623209  0.02012153]
 [ 0.00032484  0.00000696  0.00009494  0.00000173  0.00524908  0.00013703
   0.99389535  0.00000792  0.00001284  0.0002693 ]
 [ 0.00000008  0.00002813  0.00001755  0.00018718  0.00000757  0.00000504
   0.          0.99707794  0.00000513  0.00267133]
 [ 0.00005055  0.00000088  0.00000517  0.00001209  0.00011905  0.00017673
   0.9996233   0.00000001  0.0000118   0.00000046]
 [ 0.00000086  0.00008236  0.00056131  0.00142354  0.03011246  0.00053029
   0.00003921  0.00042062  0.00383697  0.96299237]
 [ 0.00243462  0.00020083  0.00133704  0.00856828  0.00002706  0.00043899
   0.00040024  0.0000254   0.98525745  0.00131009]
 [ 0.00023717  0.0000004   0.00020542  0.00002143  0.00141978  0.00002286
   0.0000046   0.00094264  0.00021614  0.99692959]
 [ 0.00000199  0.0000018   0.00002

INFO:tensorflow:global_step/sec: 3.53815
INFO:tensorflow:probabilities = [[ 0.00002928  0.99016094  0.00011666  0.00005071  0.00071295  0.00000593
   0.00008244  0.00603003  0.0027691   0.00004189]
 [ 0.00000075  0.00000013  0.00000188  0.00171482  0.00074917  0.00102634
   0.00000015  0.00029888  0.00084228  0.99536562]
 [ 0.00000596  0.00030318  0.00211886  0.00116956  0.00850121  0.00004131
   0.00000287  0.02430156  0.00064074  0.96291476]
 [ 0.00000324  0.00000056  0.00013935  0.00000006  0.00005732  0.00001267
   0.99978536  0.00000002  0.00000092  0.00000051]
 [ 0.00000384  0.00000182  0.00000249  0.00007491  0.00000093  0.99975723
   0.00009786  0.00000048  0.00005701  0.00000345]
 [ 0.00014862  0.00000199  0.0000431   0.00049372  0.00000011  0.97288203
   0.00003938  0.00000029  0.0263902   0.00000055]
 [ 0.00034016  0.00001187  0.0057018   0.01524847  0.00297873  0.00621783
   0.00003387  0.01900133  0.18968917  0.76077682]
 [ 0.00000341  0.00000061  0.00024928  0.99964571  0

INFO:tensorflow:loss = 0.0778299, step = 19901 (28.263 sec)
INFO:tensorflow:probabilities = [[ 0.00000395  0.00000189  0.00003294  0.01802482  0.          0.98191476
   0.          0.00000026  0.00002125  0.00000014]
 [ 0.00000146  0.00145436  0.00312873  0.00092477  0.00000148  0.00000401
   0.00000002  0.99422896  0.00004655  0.0002096 ]
 [ 0.99987459  0.00000025  0.00001902  0.00000002  0.00000019  0.00001189
   0.0000887   0.00000021  0.00000054  0.00000442]
 [ 0.00003272  0.00000118  0.00003004  0.00000024  0.00000092  0.00011387
   0.99976808  0.00000009  0.00005197  0.00000093]
 [ 0.00003848  0.00001589  0.00000934  0.01401335  0.00001488  0.93203545
   0.00000031  0.00007858  0.00023474  0.053559  ]
 [ 0.00000148  0.0000025   0.00000876  0.00002279  0.99904817  0.00000066
   0.00002792  0.00046501  0.00004692  0.00037591]
 [ 0.00000036  0.00083083  0.99374479  0.00099455  0.00000001  0.00000356
   0.00000006  0.00000001  0.00442578  0.00000003]
 [ 0.000128    0.00000255  0.0002

INFO:tensorflow:Saving checkpoints for 20000 into /tmp/mnist_convnet_model/model.ckpt.
INFO:tensorflow:Loss for final step: 0.0981847.
INFO:tensorflow:Starting evaluation at 2018-03-08-13:02:39
INFO:tensorflow:Restoring parameters from /tmp/mnist_convnet_model/model.ckpt-20000
INFO:tensorflow:Finished evaluation at 2018-03-08-13:02:46
INFO:tensorflow:Saving dict for global step 20000: accuracy = 0.9698, global_step = 20000, loss = 0.102739
{'accuracy': 0.9698, 'loss': 0.10273933, 'global_step': 20000}
